In [ ]:
import torch
from hydra import compose, initialize
from PIL import Image 

# Ensure that the necessary repository is cloned and installed. You may need to run: 
# git clone git@github.com:WongKinYiu/YOLO.git
# cd YOLO 
# pip install .
from yolo import AugmentationComposer, bbox_nms, Config, create_model, custom_logger, draw_bboxes, Vec2Box

In [ ]:
CONFIG_PATH = "../yolo/config"
CONFIG_NAME = "config"
MODEL = "v9-c"

DEVICE = 'cuda:0'
CLASS_NUM = 80
IMAGE_PATH = '../demo/images/inference/image.png'

custom_logger()
device = torch.device(DEVICE)

In [ ]:
with initialize(config_path=CONFIG_PATH, version_base=None, job_name="notebook_job"):
    cfg: Config = compose(config_name=CONFIG_NAME, overrides=["task=inference", f"task.data.source={IMAGE_PATH}", f"model={MODEL}"])
    model = create_model(cfg.model, class_num=CLASS_NUM).to(device)
    transform = AugmentationComposer([], cfg.image_size)
    vec2box = Vec2Box(model, cfg.image_size, device)

In [ ]:
pil_image = Image.open(IMAGE_PATH)
image, bbox, rev_tensor = transform(pil_image)
image = image.to(device)[None]
rev_tensor = rev_tensor.to(device)

In [ ]:
with torch.no_grad():
    predict = model(image)
    pred_class, _, pred_bbox = vec2box(predict["Main"])

pred_bbox = (pred_bbox / rev_tensor[0] - rev_tensor[None, None, 1:]) 
pred_bbox = bbox_nms(pred_class, pred_bbox, cfg.task.nms)
draw_bboxes(pil_image, pred_bbox, idx2label=cfg.class_list)

Sample Output:

![image](../demo/images/output/visualize.png)